In [1]:
from tensorflow import keras
import tensorflow as tf
import os
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import seaborn as sns
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score, f1_score

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout, GRU, Bidirectional, Flatten
from tensorflow.keras.optimizers import SGD
from tensorflow.random import set_seed

set_seed(2024)
np.random.seed(2024)


import csv
import librosa
import librosa.display
import matplotlib.pyplot as plt
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

train_dir = os.path.abspath('../data/train/train')
test_dir = os.path.abspath('../data/test/test')

classes = os.listdir(train_dir + '/audio')
# classes.remove("_background_noise_")

X_train = np.load(train_dir + "/X_train.npy")
y_train = np.load(train_dir + "/y_train.npy")

X_val = np.load(train_dir + "/X_val.npy")
y_val = np.load(train_dir + "/y_val.npy")

X_train = X_train.reshape((-1, X_train.shape[1], X_train.shape[2]))
X_val = X_val.reshape((-1, X_val.shape[1], X_val.shape[2]))

X_test = np.load(test_dir + '/X_test.npy')
X_files = np.loadtxt(test_dir + '/X_files.txt', delimiter=" ", dtype='str')

def plot_loss(history_df, name, idx):
    plt.figure()
    plt.plot(history_df['loss'])
    plt.plot(history_df['val_loss'])
    plt.title(f'{name}: loss')
    plt.ylabel('loss')
    plt.xlabel('epoch')
    plt.legend(['train', 'test'], loc='upper right')
    path = f'train_history/{name}/{idx}_loss.png'
    plt.savefig(path)
    print(f'Loss plot is saved to: {path}')
    plt.close()


# LSTM

In [4]:
input_shape = (122, 85)
epochs = 100
batch_size = 32


model_lstm = Sequential()
model_lstm.add(LSTM(units=125, activation="tanh", input_shape=input_shape))
model_lstm.add(Dense(units=len(classes)))
# Compiling the model
model_lstm.compile(optimizer="RMSprop", loss="mse")

print(model_lstm.summary())

# Model training
history = model_lstm.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_data=(X_val, y_val))

history_df = pd.DataFrame(history.history) 
hist_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_history.csv'
with open(hist_csv_file, mode='w') as f:
    history_df.to_csv(f)

plot_loss(history_df, 'LSTM', str(0))

# Check validation accuracy and f1
y_pred = np.argmax(model_lstm.predict(X_val), axis=-1)
accuracy = accuracy_score(y_val, y_pred)

f1 = f1_score(y_val, y_pred, average='macro')
metrics_df = pd.DataFrame({'accuracy': [accuracy], 'f1': [f1]}) 
metrics_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_metrics.csv'
with open(metrics_csv_file, mode='w') as f:
    metrics_df.to_csv(f)
print(metrics_df)

# Confusion Matrix
cm = confusion_matrix(y_val, y_pred)
accuracy = accuracy_score(y_val, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 30), yticklabels=range(0, 30))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'LSTM Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'train_history/LSTM/0_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

# Prepare submission
submission_df = pd.DataFrame({'fname': [], 'label': []}) 
for ind, test_file in enumerate(X_files):
    y_pred = np.argmax(model_lstm.predict(np.array([X_test[ind]])), axis=-1)
    submission_df.loc[len(submission_df.index)] = [X_files[ind], classes[y_pred[0]]]
submission_csv_file = 'train_history/' + 'LSTM' + '/' + str(0) + '_submission.csv'
with open(submission_csv_file, mode='w') as f:
    submission_df.to_csv(f, index=False, lineterminator='\n')
print('Submission saved.')

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_1 (LSTM)               (None, 125)               105500    
                                                                 
 dense_1 (Dense)             (None, 30)                3780      
                                                                 
Total params: 109,280
Trainable params: 109,280
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/100
1597/1597 [==============================] - 80s 49ms/step - loss: 74.5624 - val_loss: 62.1896
Epoch 2/100
1597/1597 [==============================] - 78s 49ms/step - loss: 49.7200 - val_loss: 44.3887
Epoch 3/100
1597/1597 [==============================] - 80s 50ms/step - loss: 31.4479 - val_loss: 30.6638
Epoch 4/100
1597/1597 [==============================] - 81s 51ms/step - loss: 23.2172 - val_loss: 21.4600
Epoch 5/100

MemoryError: Unable to allocate 1.63 MiB for an array with shape (2, 106512) and data type object

# GRU

In [2]:
input_shape = (122, 85)
epochs = 50
batch_size = 32

model_gru = Sequential()
model_gru.add(Dropout(0.2, input_shape=input_shape))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(GRU(units=125, return_sequences=True))
model_gru.add(Dropout(0.2))
model_gru.add(Flatten()),
model_gru.add(Dense(units=125, activation="sigmoid"))
model_gru.add(Dropout(0.2))
model_gru.add(Dense(units=len(classes), activation="softmax"))
# Compiling the model
model_gru.compile(optimizer="adam", loss="mse")

print(model_gru.summary())

# Model training
history = model_gru.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_data=(X_val, y_val))

history_df = pd.DataFrame(history.history) 
hist_csv_file = 'train_history/' + 'GRU' + '/' + str(1) + '_history.csv'
with open(hist_csv_file, mode='w') as f:
    history_df.to_csv(f)

plot_loss(history_df, 'GRU', str(1))

# Check validation accuracy and f1
y_pred = np.argmax(model_gru.predict(X_val), axis=-1)
accuracy = accuracy_score(y_val, y_pred)

f1 = f1_score(y_val, y_pred, average='macro')
metrics_df = pd.DataFrame({'accuracy': [accuracy], 'f1': [f1]}) 
metrics_csv_file = 'train_history/' + 'GRU' + '/' + str(1) + '_metrics.csv'
with open(metrics_csv_file, mode='w') as f:
    metrics_df.to_csv(f)
print(metrics_df)

# Confusion Matrix
cm = confusion_matrix(y_val, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 30), yticklabels=range(0, 30))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'GRU Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'train_history/GRU/1_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

# Prepare submission
# submission_df = pd.DataFrame({'fname': [], 'label': []})
# # y_pred = np.argmax(model_gru.predict(X_test), axis=-1)
# for ind, test_file in enumerate(X_files):
#     if ind%2000 == 0:
#         print("{} done!".format(ind))
#     y_pred = np.argmax(model_gru.predict(np.array([X_test[ind]])), axis=-1)
#     submission_df.loc[len(submission_df.index)] = [X_files[ind], classes[y_pred[0]]]
# submission_csv_file = 'train_history/' + 'GRU' + '/' + str(0) + '_submission.csv'
# with open(submission_csv_file, mode='w') as f:
#     submission_df.to_csv(f, index=False, lineterminator='\n')
# print('Submission saved.')

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dropout (Dropout)           (None, 122, 85)           0         
                                                                 
 gru (GRU)                   (None, 122, 125)          79500     
                                                                 
 dropout_1 (Dropout)         (None, 122, 125)          0         
                                                                 
 gru_1 (GRU)                 (None, 122, 125)          94500     
                                                                 
 dropout_2 (Dropout)         (None, 122, 125)          0         
                                                                 
 gru_2 (GRU)                 (None, 122, 125)          94500     
                                                                 
 dropout_3 (Dropout)         (None, 122, 125)          0

# Transformer

# Prepare silence

In [ ]:
from pydub import AudioSegment

def split_and_save_silence(original, name):
    for i in range(int(len(original) / 1000) - 1):
        t1 = i * 1000
        t2 = (i+1) * 1000
        newAudio = original[t1:t2]
        newAudio.export(f'../data/train/train/audio/silence/{name}_{i}.wav', format="wav")

split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/doing_the_dishes.wav')), 'doing_the_dishes')
split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/dude_miaowing.wav')), 'dude_miaowing')
split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/white_noise.wav')), 'white_noise')
split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/exercise_bike.wav')), 'exercise_bike')
split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/pink_noise.wav')), 'pink_noise')
split_and_save_silence(AudioSegment.from_wav(os.path.abspath('../data/train/train/_background_noise_/running_tap.wav')), 'running_tap')

In [2]:
from transformers import AutoFeatureExtractor, AutoModelForAudioClassification, TrainingArguments, Trainer, pipeline
import evaluate
from datasets import load_dataset, Audio, ClassLabel, concatenate_datasets
import os

train_dir = os.path.abspath('../data/train/train')
dataset = load_dataset("audiofolder", data_dir="../data/train/train/audio")
labels = dataset["train"].features["label"].names
# print(labels)
label2id, id2label = dict(), dict()
for i, label in enumerate(labels):
    label2id[label] = str(i)
    id2label[str(i)] = label

known_classes = ['yes', 'no', 'up', 'down', 'left', 'right', 'on', 'off', 'stop', 'go', 'silence', 'unknown']

def rename_unknown_labels(sample):
    if id2label[str(sample["label"])] not in known_classes:
        sample["new_label"] = known_classes.index('unknown')
    else:
        sample["new_label"] = known_classes.index(id2label[str(sample["label"])])
    return sample

dataset['train'] = dataset['train'].map(rename_unknown_labels, remove_columns='label')
dataset['train'] = dataset['train'].cast_column("new_label", ClassLabel(num_classes=len(known_classes), names=known_classes))
dataset['train'] = dataset['train'].rename_column("new_label", "label")

# Reduce number of unknown
dataset_unknown = dataset['train'].filter(lambda example: example["label"] == known_classes.index('unknown'))
dataset['train'] = dataset['train'].filter(lambda example: example["label"] != known_classes.index('unknown'))
dataset_unknown_split = dataset_unknown.train_test_split(test_size=0.05)
dataset['train'] = concatenate_datasets([dataset['train'], dataset_unknown_split['test']])
dataset = dataset['train'].train_test_split(test_size=0.2)

# Identify new label mappings
labels = dataset["train"].features["label"].names
label2id, id2label = dict(), dict()
for i, label in enumerate(labels):
    label2id[label] = str(i)
    id2label[str(i)] = label
id2label


c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


{'0': 'yes',
 '1': 'no',
 '2': 'up',
 '3': 'down',
 '4': 'left',
 '5': 'right',
 '6': 'on',
 '7': 'off',
 '8': 'stop',
 '9': 'go',
 '10': 'silence',
 '11': 'unknown'}

## facebook/wav2vec2-base

In [59]:
feature_extractor = AutoFeatureExtractor.from_pretrained(
    "facebook/wav2vec2-base")

def preprocess_function(examples):
    audio_arrays = [x["array"] for x in examples["audio"]]
    inputs = feature_extractor(
      audio_arrays,
      sampling_rate=feature_extractor.sampling_rate,
      max_length=16000, truncation=True
    )
    return inputs
 
 
encoded_dataset = dataset.map(
    preprocess_function, remove_columns="audio", batched=True)
# encoded_dataset = encoded_dataset.rename_column("intent_class", "label")

encoded_dataset['train']


c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\transformers\configuration_utils.py:363: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(
Map: 100%|██████████| 5226/5226 [00:03<00:00, 1574.70 examples/s]


Dataset({
    features: ['label', 'input_values'],
    num_rows: 20900
})

In [60]:
accuracy = evaluate.load("accuracy")
def compute_metrics(eval_pred):
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=eval_pred.label_ids)


In [61]:
import numpy as np

num_labels = len(id2label)
model = AutoModelForAudioClassification.from_pretrained(
    "facebook/wav2vec2-base", num_labels=num_labels, 
  label2id=label2id, id2label=id2label
)
 
training_args = TrainingArguments(
    output_dir="GFG_commands_reduced_unknown",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    # increase this if you have better machine resources
    learning_rate=4e-4,
    # increase this if you have better machine resources
    per_device_train_batch_size=32,
    gradient_accumulation_steps=4,
    # increase this if you have better machine resources
    per_device_eval_batch_size=32,
    # increase this if you have better machine resources
    num_train_epochs=8,
    warmup_ratio=0.1,
    # increase this if you have better machine resources
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    fp16=True,                             # set to False if you don't have GPU
)
 
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=encoded_dataset["train"].with_format("torch"),
    eval_dataset=encoded_dataset["test"].with_format("torch"),
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)
 
trainer.train()


Some weights of Wav2Vec2ForSequenceClassification were not initialized from the model checkpoint at facebook/wav2vec2-base and are newly initialized: ['classifier.bias', 'classifier.weight', 'projector.bias', 'projector.weight', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
  1%|          | 10/1304 [00:06<12:47,  1.69it/s]

{'loss': 2.4824, 'grad_norm': 0.6286147236824036, 'learning_rate': 2.4427480916030535e-05, 'epoch': 0.06}


  2%|▏         | 20/1304 [00:12<12:49,  1.67it/s]

{'loss': 2.4414, 'grad_norm': 1.3282233476638794, 'learning_rate': 5.1908396946564884e-05, 'epoch': 0.12}


  2%|▏         | 30/1304 [00:18<12:43,  1.67it/s]

...

100%|██████████| 1304/1304 [14:27<00:00,  1.58it/s]

{'eval_loss': 0.09926186501979828, 'eval_accuracy': 0.9734022196708764, 'eval_runtime': 7.5186, 'eval_samples_per_second': 695.08, 'eval_steps_per_second': 21.813, 'epoch': 7.98}


100%|██████████| 1304/1304 [14:28<00:00,  1.50it/s]

{'train_runtime': 868.8244, 'train_samples_per_second': 192.444, 'train_steps_per_second': 1.501, 'train_loss': 0.5409899705026778, 'epoch': 7.98}


TrainOutput(global_step=1304, training_loss=0.5409899705026778, metrics={'train_runtime': 868.8244, 'train_samples_per_second': 192.444, 'train_steps_per_second': 1.501, 'total_flos': 1.51359445138176e+18, 'train_loss': 0.5409899705026778, 'epoch': 7.9755351681957185})

## MIT/ast-finetuned-speech-commands-v2

In [5]:
feature_extractor = AutoFeatureExtractor.from_pretrained(
    "MIT/ast-finetuned-speech-commands-v2")

def preprocess_function(examples):
    audio_arrays = [x["array"] for x in examples["audio"]]
    inputs = feature_extractor(
      audio_arrays,
      sampling_rate=feature_extractor.sampling_rate,
      max_length=16000, truncation=True
    )
    return inputs
 
 
encoded_dataset = dataset.map(
    preprocess_function, remove_columns="audio", batched=True)
# encoded_dataset = encoded_dataset.rename_column("intent_class", "label")

encoded_dataset['train']

accuracy = evaluate.load("accuracy")
def compute_metrics(eval_pred):
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=eval_pred.label_ids)

import numpy as np

num_labels = len(id2label)
model = AutoModelForAudioClassification.from_pretrained(
    "MIT/ast-finetuned-speech-commands-v2", num_labels=num_labels, 
  label2id=label2id, id2label=id2label, ignore_mismatched_sizes=True
)
 
training_args = TrainingArguments(
    output_dir="MIT_commands",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    # increase this if you have better machine resources
    learning_rate=4e-4,
    # increase this if you have better machine resources
    per_device_train_batch_size=32,
    gradient_accumulation_steps=4,
    # increase this if you have better machine resources
    per_device_eval_batch_size=32,
    # increase this if you have better machine resources
    num_train_epochs=8,
    warmup_ratio=0.1,
    # increase this if you have better machine resources
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    fp16=True,                             # set to False if you don't have GPU
)
 
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=encoded_dataset["train"].with_format("torch"),
    eval_dataset=encoded_dataset["test"].with_format("torch"),
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)
 
trainer.train()

c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Map: 100%|██████████| 5226/5226 [00:09<00:00, 523.09 examples/s]
Some weights of ASTForAudioClassification were not initialized from the model checkpoint at MIT/ast-finetuned-speech-commands-v2 and are newly initialized because the shapes did not match:
- classifier.dense.bias: found shape torch.Size([35]) in the checkpoint and torch.Size([12]) in the model instantiated
- classifier.dense.weight: found shape torch.Size([35, 768]) in the checkpoint and torch.Size([12, 768]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
  1%|          | 10/1304 [00:08<16:22,  1.32it/s]

{'loss': 2.4709, 'grad_norm': 6.026375770568848, 'learning_rate': 3.053435114503817e-05, 'epoch': 0.06}


  2%|▏         | 20/1304 [00:15<16:06,  1.33it/s]

{'loss': 1.2982, 'grad_norm': 3.5650546550750732, 'learning_rate': 6.106870229007635e-05, 'epoch': 0.12}


  2%|▏         | 30/1304 [00:23<16:02,  1.32it/s]

...

                                                   
100%|██████████| 1304/1304 [19:47<00:00,  1.21it/s]Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 128}


{'eval_loss': 0.10480619221925735, 'eval_accuracy': 0.9770378874856487, 'eval_runtime': 16.462, 'eval_samples_per_second': 317.459, 'eval_steps_per_second': 9.962, 'epoch': 7.98}


100%|██████████| 1304/1304 [19:47<00:00,  1.10it/s]

{'train_runtime': 1187.9624, 'train_samples_per_second': 140.745, 'train_steps_per_second': 1.098, 'train_loss': 0.0826756409183716, 'epoch': 7.98}


TrainOutput(global_step=1304, training_loss=0.0826756409183716, metrics={'train_runtime': 1187.9624, 'train_samples_per_second': 140.745, 'train_steps_per_second': 1.098, 'total_flos': 1.3992439943984579e+18, 'train_loss': 0.0826756409183716, 'epoch': 7.9755351681957185})

# Submission preparation

In [8]:
# audio_file='../data/test/test/audio/clip_000a96d0a.wav'
import csv

classifier = pipeline("audio-classification", model="MIT_commands/checkpoint-1304")

def predict(audio_file, classifier):
    prediction = classifier(audio_file)
    if len(prediction) == 0:
        print(f'no prediction for {audio_file}')
        return 'unknown'
    return prediction[0]['label']


submission_df = pd.DataFrame({'fname': [], 'label': []})
classifier = pipeline("audio-classification", model="MIT_commands/checkpoint-1304")
submission_csv_file = 'MIT_commands/' + 'checkpoint-1304' + '/' + str(0) + '_submission.csv'

for ind, test_file in enumerate(X_files):
    if ind%2000 == 0:
        print("{} done!".format(ind))
    label_pred = predict(test_dir + '/audio/' + test_file, classifier)
    with open(submission_csv_file, 'a', newline='') as csvfile:
        writer = csv.writer(csvfile)
        writer.writerow([X_files[ind], label_pred])

print('Submission saved.')

0 done!
2000 done!
4000 done!
6000 done!
8000 done!
10000 done!
12000 done!
14000 done!
16000 done!
18000 done!
20000 done!
22000 done!
24000 done!
26000 done!
28000 done!
30000 done!
32000 done!
34000 done!
36000 done!
38000 done!
40000 done!
42000 done!
44000 done!
46000 done!
48000 done!
50000 done!
52000 done!
54000 done!
56000 done!
58000 done!
60000 done!
62000 done!
64000 done!
66000 done!
68000 done!
70000 done!
72000 done!
74000 done!
76000 done!
78000 done!
80000 done!
82000 done!
84000 done!
86000 done!
88000 done!
90000 done!
92000 done!
94000 done!
96000 done!
98000 done!
100000 done!
102000 done!
104000 done!
106000 done!
108000 done!
110000 done!
112000 done!
114000 done!
116000 done!
118000 done!
120000 done!
122000 done!
124000 done!
126000 done!
128000 done!
130000 done!
132000 done!
134000 done!
136000 done!
138000 done!
140000 done!
142000 done!
144000 done!
146000 done!
148000 done!
150000 done!
152000 done!
154000 done!
156000 done!
158000 done!


Exception in thread Thread-169259 (_readerthread):
Traceback (most recent call last):
  File "c:\Users\megav\anaconda3\envs\iml-10\lib\threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\ipykernel\ipkernel.py", line 761, in run_closure
    _threading_Thread_run(self)
  File "c:\Users\megav\anaconda3\envs\iml-10\lib\threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "c:\Users\megav\anaconda3\envs\iml-10\lib\subprocess.py", line 1515, in _readerthread
    buffer.append(fh.read())
MemoryError


# Accuracy and confusion matrix

In [6]:
classifier = pipeline("audio-classification", model="MIT_commands/checkpoint-1304")

y_true = []
y_pred = []

def predict(audio_file, classifier):
    prediction = classifier(audio_file)
    if len(prediction) == 0:
        print(f'no prediction for {audio_file}')
        return 'unknown'
    return prediction[0]['label']

for ind, file in enumerate(dataset['test']):
    if ind%2000 == 0:
        print("{} done!".format(ind))
    y_true.append(file['label'])
    predicted_label = predict(file['audio']['path'], classifier)
    y_pred.append(label2id[predicted_label])

y_pred = [int(x) for x in y_pred]
accuracy = accuracy_score(y_true, y_pred)

# Confusion Matrix
cm = confusion_matrix(y_true, y_pred)
print(f'Accuracy: {accuracy * 100:.2f}%')

plt.figure(figsize=(8, 6))
sns.heatmap(cm, annot=True, fmt="d", cmap="Blues", xticklabels=range(0, 12), yticklabels=range(0, 12))
plt.xlabel('Predicted')
plt.ylabel('True')
plt.title(f'Transformer Confusion Matrix. Accuracy: {accuracy * 100:.2f}%')
path = f'MIT_commands/checkpoint-1304/0_confusion_matrix.png'
plt.savefig(path)
print(f'Confusion matrix is saved to: {path}')
plt.close()

0 done!


c:\Users\megav\anaconda3\envs\iml-10\lib\site-packages\transformers\models\audio_spectrogram_transformer\feature_extraction_audio_spectrogram_transformer.py:118: UserWarning: The given NumPy array is not writable, and PyTorch does not support non-writable tensors. This means writing to this tensor will result in undefined behavior. You may want to copy the array to protect its data or make it writable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at ..\torch\csrc\utils\tensor_numpy.cpp:212.)
  waveform = torch.from_numpy(waveform).unsqueeze(0)


2000 done!
4000 done!
Accuracy: 97.70%
Confusion matrix is saved to: MIT_commands/checkpoint-1304/0_confusion_matrix.png
